In [37]:
import numpy as np
import pandas as pd
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots

# Function to load data and fix its structure
def fix_data(df):
    df['Date'] = pd.to_datetime(df['Date'])
    df.set_index('Date', inplace=True)

# Function to perform an exploratory check of the data
def exploratory_check(df):
    print(df.head())  # Print the first few rows
    # print(df.dtypes)  # Print the data types of the columns

# Function to process a cryptocurrency data file
def process_crypto_data(file_path):
    df = pd.read_csv(file_path)
    fix_data(df)
    exploratory_check(df)
    return df

# Function to process a stock data file
def process_stock_data(file_path):
    df = pd.read_csv(file_path)

    # Reverse the DataFrame if it's in reverse chronological order
    df = df.iloc[::-1]

    # Convert price columns to float and rename columns to match crypto data
    df.rename(columns={'Close/Last': 'Close'}, inplace=True)
    for col in ['Close', 'Open', 'High', 'Low']:
        if df[col].dtype == 'object':
            df[col] = df[col].str.replace('$', '').astype(float)

    fix_data(df)
    exploratory_check(df)
    return df

# File paths for the cryptocurrency data
crypto_files = {
    'BTC': '../historical_yahoo/BTC-USD.csv',
    'ETH': '../historical_yahoo/ETH-USD.csv',
    'DOGE': '../historical_yahoo/DOGE-USD.csv'
}

# File paths for the stock data
stock_files = {
    'APPLE': '../historical_yahoo/APPLE-USD.csv',
    'TESLA': '../historical_yahoo/TESLA-USD.csv',
    'AMAZON': '../historical_yahoo/AMAZON-USD.csv',
}

# Process and check cryptocurrency data
btc_data = process_crypto_data(crypto_files['BTC'])
eth_data = process_crypto_data(crypto_files['ETH'])
doge_data = process_crypto_data(crypto_files['DOGE'])

# Process and check stock data
apple_data = process_stock_data(stock_files['APPLE'])
tesla_data = process_stock_data(stock_files['TESLA'])
amazon_data = process_stock_data(stock_files['AMAZON'])

# Perform exploratory checks
exploratory_check(btc_data)
exploratory_check(apple_data)


                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2014-09-17  465.864014  468.174011  452.421997  457.334015  457.334015   
2014-09-18  456.859985  456.859985  413.104004  424.440002  424.440002   
2014-09-19  424.102997  427.834991  384.532013  394.795990  394.795990   
2014-09-20  394.673004  423.295990  389.882996  408.903992  408.903992   
2014-09-21  408.084991  412.425995  393.181000  398.821014  398.821014   

              Volume  
Date                  
2014-09-17  21056800  
2014-09-18  34483200  
2014-09-19  37919700  
2014-09-20  36863600  
2014-09-21  26580100  
                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2017-11-09  308.644989  329.451996  307.056000  320.884003  320.884003   
2017-11-10  320.670990  324.717987  294.541992  299.252991  299.252991   
2017-11-11  298.585999  

In [38]:
def simulate_investment_for_each_date(df, daily_investment=1):
    simulation_results = []

    for start_date in df.index:
        df_filtered = df[df.index >= start_date]
        df_filtered = df_filtered.copy()  # To avoid SettingWithCopyWarning
        df_filtered['Crypto_Bought'] = daily_investment / df_filtered['Open']
        df_filtered['Cumulative_Crypto'] = df_filtered['Crypto_Bought'].cumsum()
        df_filtered['Cumulative_$Invested'] = daily_investment * np.arange(1, len(df_filtered) + 1)
        df_filtered['Cumulative_Value_$'] = df_filtered['Cumulative_Crypto'] * df_filtered['Close']
        df_filtered['Cumulative_ROI'] = ((df_filtered['Cumulative_Value_$'] - df_filtered['Cumulative_$Invested']) / df_filtered['Cumulative_$Invested']) * 100

        simulation_results.append(df_filtered.iloc[-1][['Cumulative_$Invested', 'Cumulative_Crypto', 'Cumulative_Value_$', 'Cumulative_ROI']])

    simulation_df = pd.DataFrame(simulation_results, index=df.index)
    return simulation_df

# Load and simulate for BTC, ETH, and DOGE
btc_data = process_crypto_data(crypto_files['BTC'])
btc_simulation = simulate_investment_for_each_date(btc_data)

eth_data = process_crypto_data(crypto_files['ETH'])
eth_simulation = simulate_investment_for_each_date(eth_data)

doge_data = process_crypto_data(crypto_files['DOGE'])
doge_simulation = simulate_investment_for_each_date(doge_data)

# Function to create a plot for each metric
def create_plot(metric_name):
    fig = go.Figure()
    for crypto_simulation, name in zip([btc_simulation, eth_simulation, doge_simulation], ['BTC', 'ETH', 'DOGE']):
        fig.add_trace(go.Scatter(x=crypto_simulation.index, y=crypto_simulation[metric_name], mode='lines', name=f'{name} {metric_name}'))
    fig.update_layout(title=f"{metric_name} Over Different Start Dates", xaxis_title="Start Date", yaxis_title=metric_name, width=1200, height=600, legend=dict(x=0, y=1))
    fig.show()

# Creating and showing each plot
create_plot('Cumulative_$Invested')
create_plot('Cumulative_Crypto')
create_plot('Cumulative_Value_$')
create_plot('Cumulative_ROI')

                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2014-09-17  465.864014  468.174011  452.421997  457.334015  457.334015   
2014-09-18  456.859985  456.859985  413.104004  424.440002  424.440002   
2014-09-19  424.102997  427.834991  384.532013  394.795990  394.795990   
2014-09-20  394.673004  423.295990  389.882996  408.903992  408.903992   
2014-09-21  408.084991  412.425995  393.181000  398.821014  398.821014   

              Volume  
Date                  
2014-09-17  21056800  
2014-09-18  34483200  
2014-09-19  37919700  
2014-09-20  36863600  
2014-09-21  26580100  
                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2017-11-09  308.644989  329.451996  307.056000  320.884003  320.884003   
2017-11-10  320.670990  324.717987  294.541992  299.252991  299.252991   
2017-11-11  298.585999  

In [45]:
def simulate_investment_for_each_date(df, daily_investment=1):
    simulation_results = []

    for start_date in df.index:
        df_filtered = df[df.index >= start_date]
        df_filtered = df_filtered.copy()  # To avoid SettingWithCopyWarning
        df_filtered['Asset_Bought'] = daily_investment / df_filtered['Open']
        df_filtered['Cumulative_Asset'] = df_filtered['Asset_Bought'].cumsum()
        df_filtered['Cumulative_$Invested'] = daily_investment * np.arange(1, len(df_filtered) + 1)
        df_filtered['Cumulative_Value_$'] = df_filtered['Cumulative_Asset'] * df_filtered['Close']
        df_filtered['Cumulative_ROI'] = ((df_filtered['Cumulative_Value_$'] - df_filtered['Cumulative_$Invested']) / df_filtered['Cumulative_$Invested']) * 100

        simulation_results.append(df_filtered.iloc[-1][['Cumulative_$Invested', 'Cumulative_Asset', 'Cumulative_Value_$', 'Cumulative_ROI']])

    simulation_df = pd.DataFrame(simulation_results, index=df.index)
    return simulation_df

# Load and simulate for both cryptocurrencies and stocks
simulations = {}
for file_name, file_path in {**crypto_files, **stock_files}.items():
    data = process_crypto_data(file_path) if file_name in crypto_files else process_stock_data(file_path)
    simulations[file_name] = simulate_investment_for_each_date(data)

# Function to create a plot for each metric
def create_plot(metric_name):
    fig = go.Figure()
    for name, simulation in simulations.items():
        fig.add_trace(go.Scatter(x=simulation.index, y=simulation[metric_name], mode='lines', name=f'{name} {metric_name}'))
    fig.update_layout(title=f"Value from start invest $1 daily", xaxis_title="Start Date", yaxis_title=metric_name, width=1200, height=600, legend=dict(x=0, y=1))
    fig.show()

# Creating and showing each plot
create_plot('Cumulative_$Invested')
create_plot('Cumulative_Asset')
create_plot('Cumulative_Value_$')
create_plot('Cumulative_ROI')


                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2014-09-17  465.864014  468.174011  452.421997  457.334015  457.334015   
2014-09-18  456.859985  456.859985  413.104004  424.440002  424.440002   
2014-09-19  424.102997  427.834991  384.532013  394.795990  394.795990   
2014-09-20  394.673004  423.295990  389.882996  408.903992  408.903992   
2014-09-21  408.084991  412.425995  393.181000  398.821014  398.821014   

              Volume  
Date                  
2014-09-17  21056800  
2014-09-18  34483200  
2014-09-19  37919700  
2014-09-20  36863600  
2014-09-21  26580100  
                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2017-11-09  308.644989  329.451996  307.056000  320.884003  320.884003   
2017-11-10  320.670990  324.717987  294.541992  299.252991  299.252991   
2017-11-11  298.585999  

In [43]:
def simulate_daily_investment_metrics(df, daily_investment=1):
    df['Asset_Bought'] = daily_investment / df['Open']
    df['Value_End_$'] = df['Asset_Bought'] * df.iloc[-1]['Close']
    df['ROI'] = ((df['Value_End_$'] - daily_investment) / daily_investment) * 100
    return df[['Asset_Bought', 'Value_End_$', 'ROI', 'Close']]

# Load and simulate daily metrics for both cryptocurrencies and stocks
daily_metrics = {}
for file_name, file_path in {**crypto_files, **stock_files}.items():
    data = process_crypto_data(file_path) if file_name in crypto_files else process_stock_data(file_path)
    daily_metrics[file_name] = simulate_daily_investment_metrics(data)

# Function to create a plot for daily metric across multiple assets
def create_combined_daily_plot(metric_name):
    fig = go.Figure()
    for file_name, metrics in daily_metrics.items():
        metric_data = metrics[metric_name]
        fig.add_trace(go.Scatter(x=metric_data.index, y=metric_data, mode='lines', name=f'{file_name} {metric_name}'))
    fig.update_layout(title=f"Scenario: Value of $1 invested today", xaxis_title="Date", yaxis_title=metric_name, width=1200, height=600, legend=dict(x=0, y=1))
    fig.show()

# Choose which metric to plot across assets
create_combined_daily_plot('Close')
create_combined_daily_plot('Asset_Bought')
create_combined_daily_plot('Value_End_$')
create_combined_daily_plot('ROI')


                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2014-09-17  465.864014  468.174011  452.421997  457.334015  457.334015   
2014-09-18  456.859985  456.859985  413.104004  424.440002  424.440002   
2014-09-19  424.102997  427.834991  384.532013  394.795990  394.795990   
2014-09-20  394.673004  423.295990  389.882996  408.903992  408.903992   
2014-09-21  408.084991  412.425995  393.181000  398.821014  398.821014   

              Volume  
Date                  
2014-09-17  21056800  
2014-09-18  34483200  
2014-09-19  37919700  
2014-09-20  36863600  
2014-09-21  26580100  
                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2017-11-09  308.644989  329.451996  307.056000  320.884003  320.884003   
2017-11-10  320.670990  324.717987  294.541992  299.252991  299.252991   
2017-11-11  298.585999  